# S3 file system

S3 is a file storage service offered by Amazon. Just like normal internet where URL is mapped to IP addresses via registers, S3 has its own address protocol. 

Here is an example of a S3 file hosted on AWS server. 

```
s3://mast/level1/shots/11695.zarr 
```

The s3fs python package sends a request to Amazon server and if the request is valid example, permissions, the file gets downloaded. 

A guide on basic usage of S3 using S3fs: [Link](https://medium.com/@akifmalik200/setting-up-s3fs-on-ubuntu-a-beginners-guide-to-mounting-s3-buckets-f84513cd6be4)

## MinIO: an alternative
Since Amazon AWS is not a free service unless you put the credit card details, I will use [MinIO](https://min.io/), which is a S3 compatible storage. There are [several](https://min.io/open-source/download?platform=linux) ways to install MinIO on Linux.

### Download MinIO Server
```bash
wget https://dl.min.io/server/minio/release/linux-amd64/minio
chmod +x minio
```

### Start MinIO Server locally
```bash
./minio server .
```

This starts an API at: http://192.168.0.42:9000 and a Web UI at http://192.168.0.42:41779. The port numbers may vary. Enter the credentials in the web GUI to login.


![image.png](images/minui_web_ui.png)

### Install MinIO Client (mc)
Although MinIO has a web UI, it is better to use the command line interface to manipulate the files in python.

```bash
wget https://dl.min.io/client/mc/release/linux-amd64/mc
chmod +x mc
```
### Provide the server details to mc
```bash
./mc alias set local http://127.0.0.1:9000 minioadmin minioadmin
```

minioadmin is the default username and password.

### Create a Bucket
```bash
./mc mb local/my-bucket
```

An empty bucket can be seen in the web UI. 

In [9]:
import pandas

# Create dummy data
data = {
    "Name": ["Alice", "Bob", "Charlie"],
    "Age": [25, 30, 35],
    "City": ["New York", "London", "Paris"]
}

# save data to csv
df = pandas.DataFrame(data)
csv_file = "data/data.csv"
df.to_csv(csv_file, index=False)

/home/hell/anaconda3/lib/python3.9/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


In [ ]:
import s3fs

# Create a connection to the S3 bucket
fs = s3fs.S3FileSystem(
    key = 'minioadmin',
    secret = 'minioadmin',
    client_kwargs = {'endpoint_url': 'http://localhost:9000'}
)

# Create a bucket
fs.mkdir('my-bucket-2') # Create a bucket

# Upload a file to the bucket
fs.put('images/minui_web_ui.png', 'my-bucket-2/images/minui_web_ui.png') # Upload an image to the bucket

[None]

In [10]:
fs.put('data/data.csv', 'my-bucket-2/data/data.csv') # Upload a csv file to the bucket

[None]

In [11]:
print(fs.ls('s3://my-bucket-2'))

['my-bucket-2/data', 'my-bucket-2/images']


In [ ]:
# Read a file from the bucket
with fs.open('my-bucket-2/images/minui_web_ui.png', 'rb') as f:
    print(f.read())

b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x02\xd1\x00\x00\x02\xde\x08\x06\x00\x00\x00l\x9fM\xd2\x00\x00\x00\x04sBIT\x08\x08\x08\x08|\x08d\x88\x00\x00\x00\x19tEXtSoftware\x00gnome-screenshot\xef\x03\xbf>\x00\x00 \x00IDATx\x9c\xec\xdd{\\Tu\xfe\xc7\xf1\xd700$\xa8\x81x\x034 \x05\x7f\x81\x9a(\x88\x89\xabXi\x9ay\xc3[\xa9\x95v1\xcdM\xcb\xad\xd4\\u\xcb\xdars+-\xb3\x9b\x976q\xc3\x0c53M+\xd1U\x0b!\xf1\x86\xbbJ\x04\x163\xa0\xa6\x90\n\xca\xc00\xbf?f\xce0\x03\x03\x0c8\xdc\xec\xf3|<\xda\x95\x993\xe7|\xcfa\x86y\x9f\xef\xf9\x9c\xefW\xd5\xd67\xd8\x88\x10B\x08!\x84\x10\xc2a.\r\xdd\x00!\x84\x10B\x08!\x9a\x1a\xd7\x86n\x80\x10\n#\xe0\x82\nT*\xd3\x03*P)\xff\x10B\x08a\x87\x11\xa3\xe9\xff,?\x97\x1aKQ\xc9\xdfMQ\xcf\x8c\x98\xbe\xad\x8d\xca?0Z\xde\x85\xa6\xb7\xa7\n\x8c\xa6\xafx\xa3\xd1\x88J\xd5\xf4\xdf\xa3\x12\xa2E#\xa0B\xa5\x02\x17\x95\\\x18\x11B\x88\x9a1\xc7eU\xd9\xcfj\x95\x0bF\xa3\x11\xa3\xd1\x88U\xba\x16\xa2\xce\x181ZN\xdcTV\xef\xc5\n\xffR\xfa\xc8T*\x9b\xd74U\x12\xa2E\x83rQ\xb9X\x7f\xe2\x84\x10B8\x81J\xa

In [12]:
with fs.open('my-bucket-2/data/data.csv', 'rb') as f:
    print(f.read())

b'Name,Age,City\nAlice,25,New York\nBob,30,London\nCharlie,35,Paris\n'


Now if we want we can browse the bucket using the web UI or the command line interface.

![image.png](images/s3_bucket_overview.png)

And see the details of the files stored.

![image.png](images/uploaded_file.png)

[LocalStack](https://www.localstack.cloud/) is another alternative to AWS S3. It is a fully functional local AWS cloud stack.